In [1]:
import os
import glob
import json

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from tqdm import tqdm
from numpy import linalg as LA
from matplotlib.ticker import FuncFormatter
# %run ~/.mpl_set.py

import networkx as nx

from sknetwork.clustering import Louvain

In [2]:
!jupyter nbconvert --to script clustering.ipynb

[NbConvertApp] Converting notebook clustering.ipynb to script
[NbConvertApp] Writing 5124 bytes to clustering.py


In [2]:
#pip install scikit-network

Defaulting to user installation because normal site-packages is not writeable
  Using cached scikit_network-0.31.0-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (4.8 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 110.0 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 36.6/36.6 MB 49.9 MB/s eta 0:00:0000:0100:01
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
barnaba 0.1.8 requires sklearn, which is not installed.
arviz 0.11.2 requires typing-extensions<4,>=3.7.4.3, but you have typing-extensions 4.6.3 which is incompatible.
numba 0.55.1 requires numpy<1.22,>=1.18, but you have numpy 1.26.0 which is incompatible.
Note: you may need to restart the kernel to use updated packages.


In [2]:
df=pd.read_pickle("result.pkl")

In [3]:
df

pdb  \
0        /project/zerze/ayushg/argonne/configs/ICs/Q_0....   
1        /project/zerze/ayushg/argonne/configs/ICs/Q_0....   
2        /project/zerze/ayushg/argonne/configs/ICs/Q_0....   
3        /project/zerze/ayushg/argonne/configs/ICs/Q_0....   
4        /project/zerze/ayushg/argonne/configs/ICs/Q_0....   
...                                                    ...   
1357995  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...   
1357996  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...   
1357997  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...   
1357998  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...   
1357999  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...   

                                                       dcd  frame      rmsd  \
0        /project/zerze/ayushg/argonne/ddmd/rna4/test/m...      0  3.871517   
1        /project/zerze/ayushg/argonne/ddmd/rna4/test/m...      1  4.072567   
2        /project/zerze/ayushg/argonne/ddmd/rna4/test/m...      2  4.103724   
3        /project/zerze/ayushg/argonne/ddmd/rna4/test/m...      3  3.919062   
4        /project/zerze/ayushg/argonne/ddmd/rna4/test/m...      4  4.031566   
...                                                    ...    ...       ...   
1357995  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...    995  7.219865   
1357996  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...    996  7.380145   
1357997  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...    997  7.141731   
1357998  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...    998  7.351702   
1357999  /project/zerze/ayushg/argonne/ddmd/rna4/test/m...    999  7.221921   

                    Q                                         embeddings  \
0        5.036754e-01  [1.646781086921692, -0.4771463871002197, 1.058...   
1        4.837339e-01  [1.516576886177063, -0.05030802637338638, 1.26...   
2        5.703641e-01  [1.9213682413101196, -0.16811102628707886, 0.9...   
3        5.269967e-01  [2.1479034423828125, -0.1007068008184433, 1.00...   
4        5.270645e-01  [1.9867029190063477, -0.016016993671655655, 1....   
...               ...                                                ...   
1357995  1.376649e-13  [0.03651024401187897, 1.192536473274231, 0.954...   
1357996  1.935993e-14  [0.0636850893497467, 1.4230018854141235, 1.099...   
1357997  1.264189e-11  [0.09392370283603668, 1.0922075510025024, 0.97...   
1357998  3.737544e-13  [0.06389271467924118, 1.1097445487976074, 1.41...   
1357999  8.372795e-11  [-0.039575010538101196, 0.9804670214653015, 0....   

         lof_score            sys_label gpu_id  cluster_label  
0        -1.255994  md_run_2_1696508645      2            494  
1        -0.999194  md_run_2_1696508645      2            494  
2        -1.028983  md_run_2_1696508645      2            494  
3        -1.049142  md_run_2_1696508645      2            494  
4        -1.063697  md_run_2_1696508645      2            494  
...            ...                  ...    ...            ...  
1357995  -1.004653  md_run_7_1697109289      7            397  
1357996  -1.166332  md_run_7_1697109289      7             15  
1357997  -1.170684  md_run_7_1697109289      7             15  
1357998  -1.134105  md_run_7_1697109289      7            397  
1357999  -1.096284  md_run_7_1697109289      7            397  

[1358000 rows x 10 columns]

In [4]:
len(df.cluster_label.unique())

500

In [5]:
dtrajs = []    # a 2-D matrix to store the cluster no. of each frame of each simulation
for sys_label in sorted(df.sys_label.unique()): 
    sub_df = df[df['sys_label'] == sys_label]
    dtrajs.append(sub_df['cluster_label'].values)

In [6]:
#sub_df['cluster_label'].values

In [7]:
np.shape(sub_df['cluster_label'].values)

(1000,)

In [8]:
print(np.shape(dtrajs))
type(dtrajs)

(1358, 1000)


list

In [9]:
dtrajs[0][2]

494

In [10]:
def get_trans_count(dtrajs, lag=1):
    adj_sparse = {}      # dictionary
    for dtraj in dtrajs: 
        for i in range(len(dtraj) - lag): 
            transition = (dtraj[i], dtraj[i+lag])
            if transition in adj_sparse: 
                adj_sparse[transition] += 1 
            else: 
                adj_sparse[transition] = 1

    n_states = len(set(np.concatenate(dtrajs)))   # no. of macrostates i.e. clusters
    print(n_states)
    trans_count = np.zeros((n_states, n_states),dtype=int)
    for edges in adj_sparse: 
        #print(edges)
        
        trans_count[edges] = int(adj_sparse[edges])
        #print(trans_count[edges])
        print(type(adj_sparse[edges]))
        print(type(trans_count[edges]))

    trans_count = trans_count + trans_count.T    # why this? detailed balance?
    return trans_count 

def get_trans_mat(dtrajs, lag=1): 
    trans_count = get_trans_count(dtrajs, lag=lag)
    trans_mat = trans_count / np.sum(trans_count, axis=0)
    return trans_mat

In [11]:
b={}
print(type(b))
b[1,1]=1
b[2,2]=2
c=np.zeros((2,2))
print(b,c)

<class 'dict'>
{(1, 1): 1, (2, 2): 2} [[0. 0.]
 [0. 0.]]


In [12]:
a=1.
print(type(a))
type(a)


<class 'float'>


float

In [13]:
trans_mat_norm = get_trans_mat(dtrajs)
G = nx.from_numpy_array(trans_mat_norm, create_using=nx.DiGraph())
#G = nx.from_numpy_array(trans_mat_norm, create_using=nx.Graph())

500
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'nu

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.

In [14]:
G

In [15]:
cluster_info = []
for label in df.cluster_label.unique()[:]: 
    sub_df = df[df.cluster_label == label] 
    cluster_info.append({'label': int(label),  
                         'rmsd_mean': sub_df.rmsd.mean(), 
                         'rmsd_std': sub_df.rmsd.std(),
                         'Q_mean': sub_df.Q.mean(), 
                         'Q_std': sub_df.Q.std(),
                        })
#     print(sub_df.dist.count(), sub_df.dist.std(), sub_df.dist.mean())

cluster_info = pd.DataFrame(cluster_info)
cluster_info = cluster_info.sort_values('label').reset_index(drop=True)
cluster_info

label  rmsd_mean  rmsd_std
0        0   6.864686  1.152772
1        1   7.074500  1.211165
2        2   5.256840  0.609867
3        3   9.051564  0.404598
4        4   8.862396  0.378688
..     ...        ...       ...
495    495   6.842879  1.199971
496    496   3.566250  0.179966
497    497   6.922704  1.088267
498    498   8.830950  0.392558
499    499   8.789314  0.393993

[500 rows x 3 columns]

In [16]:
col_names = sorted([col for col in cluster_info.columns])
for i in sorted(G.nodes()):
    for col in col_names:
        G.nodes[i][col] = cluster_info[col][i]

In [103]:
np.set_printoptions(threshold=1000)

In [17]:
trans_count = get_trans_count(dtrajs)  # 500 X 500 matrix having info about transitions from cluster/state i to j. Here, 500 is the no. of clusters obtained through k-means
np.savetxt('trans_count.txt', trans_count)
print(trans_count.shape,type(trans_count))
print(trans_count[0])
louvain = Louvain(modularity='newman', random_state=42)
labels = louvain.fit_predict(trans_count)
print(labels.shape,type(labels))
#labels.toarray()
#len((labels))

500
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'nu

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.

In [18]:
len(set(labels))

13

In [19]:
for i in sorted(G.nodes()):
    G.nodes[i]['mod'] = labels[i]

cluster_info['mod'] = labels

In [21]:
nx.write_gexf(G, 'kmeans.gexf')
#nx.write_gpickle(G, 'kmeans.pkl')

In [22]:
df['mod'] = [labels[i] for i in df['cluster_label']]

In [29]:
df.to_pickle('./df_kmeans.pkl')

In [30]:
dtrajs_mod = []
for sys_label in sorted(df.sys_label.unique()): 
    sub_df = df[df['sys_label'] == sys_label]
    dtrajs_mod.append(sub_df['mod'].values)

In [31]:
trans_mat_mod = get_trans_mat(dtrajs_mod)
trans_mat_mod.shape
G_mod = nx.from_numpy_array(trans_mat_mod, create_using=nx.DiGraph())

13
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'numpy.int64'>
<class 'int'>
<class 'num

In [32]:
cluster_info = []
for label in df['mod'].unique()[:]: 
    sub_df = df[df['mod'] == label] 
    cluster_info.append({'mod': int(label), 
                         'rmsd_mean': sub_df.rmsd.mean(), 
                         'rmsd_std': sub_df.rmsd.std(),
                         'Q_mean': sub_df.Q.mean(), 
                         'Q_std': sub_df.Q.std(),
                        })

cluster_info = pd.DataFrame(cluster_info)
cluster_info = cluster_info.sort_values('mod').reset_index(drop=True)

In [33]:
col_names = sorted([col for col in cluster_info.columns])
for i in sorted(G_mod.nodes()):
    for col in col_names:
        G_mod.nodes[i][col] = cluster_info[col][i]

In [35]:
nx.write_gexf(G_mod, 'kmeans_mod.gexf')
#nx.write_gpickle(G_mod, 'kmeans_mod.pkl')

In [36]:
cluster_info.to_pickle('./df_kmeans_mod.pkl')